# Supplementary Material Discussion: Rewiring

We first noted that better predictions associate with a fewer number of predictors~(linear $\rho=-0.94$). This signal implies a more simple metabolic functional mode shared among many individuals within the population, i.e.,  every individual exhibits one or few growth-limiting reactions. In contrast, a larger number of predictors indicate multifarious and more complex functional modes. Thus, which reaction(s) is limiting differs across individuals. The linearity of the PGS is unable to distinguish among cases and is restricted to averaging these. 

This explication anticipates a conjecture in which a metabolism "disabled" on its capacity to react to genetic variation would paradoxically be coupled to better prediction.

## 0. Load plotting style and...

In [1]:
from matplotlib import pyplot as plt

SMALL_SIZE =  16 # 16 -> around 7pts (real Res&Size)
MEDIUM_SIZE = 20 # 20 -> around 9pts (real Res&Size)
colors = plt.style.library['seaborn-deep']['axes.prop_cycle'].by_key()['color']

# Set plot style
if 'styleDefault' not in locals():
    styleDefault = plt.rcParams.copy()
    
styleDict    = plt.style.library['seaborn-deep']
styleDict.update( { 'figure.dpi'       : 100.0        })
styleDict.update( { 'figure.facecolor' : (1,1,1,1)    })
styleDict.update( { 'axes.labelsize'   : MEDIUM_SIZE  })
styleDict.update( { 'font.size'        : SMALL_SIZE   })
styleDict.update( { 'axes.titlesize'   : SMALL_SIZE   })
styleDict.update( { 'xtick.labelsize'  : SMALL_SIZE   })
styleDict.update( { 'ytick.labelsize'  : SMALL_SIZE   })
styleDict.update( { 'legend.fontsize'  : SMALL_SIZE   })

for key, value in styleDict.items():
    plt.rcParams[key] = value

## ... load model, bounds and...

In [2]:
import cobra
import numpy as np
from tqdm import tqdm
from datetime import datetime
from multiprocessing import Pool
from matplotlib import pyplot as plt
from QuantitativeMutation import QuantitativeMutation


#Define conversion functions
rxn2mtb  = lambda REACTION:   [mtb for mtb in REACTION.metabolites ]
rxn2gene = lambda REACTION:   [gene for gene in REACTION.genes ]
mtb2rxn  = lambda METABOLITE: [rxn for rxn in METABOLITE.reactions ]
gene2rxn = lambda GENE:       [rxn for rxn in GENE.reactions]


MODEL_NAME  = 'yeast_iND750'
SOLVER_NAME = 'glpk'


#Define minimal medium...
minimal_medium = {}        
minimal_medium.update( {'EX_o2_e' :     2 }) #... oxygen
minimal_medium.update( {'EX_h2o_e' : 9999 }) #... water
minimal_medium.update( {'EX_co2_e' : 9999 }) #... carbon dioxyde
minimal_medium.update( {'EX_nh4_e' : 9999 }) #... ammonia
minimal_medium.update( {'EX_pi_e'  : 9999 }) #... phosphate
minimal_medium.update( {'EX_so4_e' : 9999 }) #... sulphate
minimal_medium.update( {'EX_k_e'   : 9999 }) #... potassium
minimal_medium.update( {'EX_na1_e' : 9999 }) #... sodium

#... and standard medium
std_medium = minimal_medium.copy()
std_medium.update( {  'EX_glc__D_e' : 20 } )


# Load specific metabolic model...
Q = QuantitativeMutation( './metabolic_models/%s.json' % MODEL_NAME , verbose=True)

#... set solver
Q.model.solver = SOLVER_NAME

#... and standard medium
Q.model.medium = std_medium

#... and load maximal bounds
Q.load_bounds('Data_1_bounds_0.10.csv')
Q.reset_dosage()
Q.apply_dosage()

#Compute solution
wt_solution  = Q.optimize()
wt_growthrate= Q.slim_optimize()
print('\nWild-type growth rate %1.3f' % Q.slim_optimize() )

Academic license - for non-commercial use only - expires 2022-08-06
Using license file /home/pyubero/gurobi.lic
Loaded model iND750 from user file.
Biomass reaction id is BIOMASS_SC4_bal
The model has 750 genes and 1266 reactions.
... number of exchange reactions:	116
... number of non-exchange reactions:	1148
Maxbounds loaded from Data_1_bounds_0.10.csv on 2022-05-15 12:27:57.005686.

Wild-type growth rate 0.514


## ... PGS data from the previous section...

In [3]:
from sklearn.linear_model import LassoCV, LinearRegression
from sklearn.metrics import r2_score, explained_variance_score, mean_squared_error
from mpl_toolkits.axes_grid1.inset_locator import inset_axes


data = np.load('Data_2_PPS_def_std.npz')
G_std    = data['G_std']  #... Genotype
f_std    = data['f_std']  #... FBA fitness
J_std    = data['J_std']  #... FBA solution fluxes
coef_std = data['B_std']  #... Effect size
R2_std  = data['R2_std'] #... PPS R2

NSAMPLES = G_std.shape[0]
NGENES   = G_std.shape[1]
NFLUXES  = J_std.shape[1]

print('Data laoded.')
print('# samples:\t%d' % NSAMPLES )
print('# genes:  \t%d' % Q.N_GENES )
print('R2 of PPS: \t%1.4f' % R2_std )


B_THRESHOLD =0.01 

#... find genes with large/small effect
large = np.argwhere(  B_THRESHOLD < np.abs(coef_std) )[:,0]
small = np.argwhere(  [ 0<np.abs(value)<B_THRESHOLD for value in coef_std] )[:,0]

#... sort the genes with descending effect size
large_ord = coef_std[large].argsort()[::-1]
small_ord = coef_std[small].argsort()[::-1]

#... concatenate both sets of large and small
values  = np.concatenate( (coef_std[large[large_ord]],coef_std[small[small_ord]]) )
indices = np.concatenate( (large[large_ord], small[small_ord]) )
labels=[ Q.model.genes[idx].name for idx in indices ]

print('N_total   = %d' % len(values) )
print('  N_large = %d' % len(large) )
print('  N_small = %d' % len(small) )
print('  N_null = %d' % (Q.N_GENES-len(large)-len(small) ) )

Data laoded.
# samples:	5000
# genes:  	750
R2 of PPS: 	0.2694
N_total   = 82
  N_large = 32
  N_small = 50
  N_null = 668


# ... and random media list...

In [4]:
import pickle as pk

with open('Data_1_random_media_list_0.10.pkl', 'rb') as handle:
        MEDIA_LIST = pk.load(handle)
        
print('Loaded %d random media.' % len(MEDIA_LIST), datetime.now() )

Loaded 10000 random media. 2022-05-15 12:27:58.701516


# ... and data computed in random environments.

In [5]:
import cobra
import pickle
import numpy as np
from tqdm import tqdm
from datetime import datetime
from multiprocessing import Pool
from matplotlib import pyplot as plt
from QuantitativeMutation import QuantitativeMutation
from sklearn.linear_model import LassoCV, LinearRegression
from sklearn.metrics import r2_score, explained_variance_score, mean_squared_error

FILENAME_OUT = 'Data_6_random_env.pkl'


with open(FILENAME_OUT,'rb') as f:
    data = pickle.load(f)
    
    
R2_pps = data['R2_pps']
BETAS  = data['BETAS']
MU     = data['MU']
wtMU   = data['wtMU']
wtJ    = data['wtJ']
vJ     = data['vJ']
mJ     = data['mJ']
PCA    = data['PCA']
SAMPLES = BETAS.shape[0]
sigmaE  = wtMU.copy()

#IDX = np.argwhere( np.isnan(wtMU))[:,0]
IDX = np.argwhere( np.isnan(wtMU) | np.all(np.isnan(vJ), axis=1))[:,0]
print('Previous data loaded successfully.')
print('Number of completed populations: %d' % (SAMPLES-len(IDX)) )
print('Number of remaining populations: %d' % len(IDX)) 
print('')


# Import media list
with open('Data_1_random_media_list_0.10.pkl', 'rb') as handle:
        MEDIA_LIST = pk.load(handle)
        
print('Loaded %d random media.' % len(MEDIA_LIST), datetime.now() )

Previous data loaded successfully.
Number of completed populations: 6709
Number of remaining populations: 3291

Loaded 10000 random media. 2022-05-15 12:27:59.881218


In [6]:
### Sort by growth rate ###

idx_sort_growth = np.argsort( sigmaE )

MU     =     MU[idx_sort_growth,:]  
BETAS  =  BETAS[idx_sort_growth,:]
vJ     =     vJ[idx_sort_growth,:]  
wtJ    =    wtJ[idx_sort_growth,:]
mJ     =     mJ[idx_sort_growth,:]
PCA    =    PCA[idx_sort_growth,:]
R2_pps = R2_pps[idx_sort_growth]
sigmaE = sigmaE[idx_sort_growth]
wtMU   =   wtMU[idx_sort_growth]  

temp_MEDIA_LIST = [ MEDIA_LIST[ii] for ii in idx_sort_growth]
MEDIA_LIST = temp_MEDIA_LIST.copy()


### Delete bad media ###
# That is, keep only media with 
# richness between [0.75, 1] relative
# to the standard medium.

idx_media_variance = np.nonzero( np.std(vJ, axis=1)>0 )[0] # media with non-null variance across the populations
idx_07_wt = np.nonzero( 0.75 < (wtMU/wt_growthrate) )[0]# media with at least 75% of wt/std fitness

idx_good_media = np.array([jj for jj in range(SAMPLES) if jj in idx_media_variance and jj in idx_07_wt])


sigmaE = sigmaE[idx_good_media]
R2_pps = R2_pps[idx_good_media]
wtMU   =   wtMU[idx_good_media]  
MU     =     MU[idx_good_media,:]  
BETAS  =  BETAS[idx_good_media,:]
vJ     =     vJ[idx_good_media,:]
mJ     =     mJ[idx_good_media,:]
wtJ    =    wtJ[idx_good_media,:]
PCA    =    PCA[idx_good_media,:]

temp_MEDIA_LIST = [ MEDIA_LIST[ii] for ii in idx_good_media]
MEDIA_LIST = temp_MEDIA_LIST.copy()

SAMPLES = BETAS.shape[0]
print(SAMPLES, len(MEDIA_LIST))
print(wtMU[0], MEDIA_LIST[0])

1724 1724
0.3855005100480926 {'EX_pepd_e': 11.375968096677752, 'EX_phe__L_e': 4.3725643690598845, 'EX_ptrc_e': 3.0053542092388783, 'EX_sbt__L_e': 9.942508927829678, 'EX_spmd_e': 13.853943400845695, 'EX_thymd_e': 0.2683289684993069, 'EX_uri_e': 2.561053096771176, 'EX_cit_e': 0.6633245585416963, 'EX_din_e': 6.567478751026615, 'EX_fmn_e': 7.485029613047061, 'EX_gam6p_e': 8.151632486887742, 'EX_o2_e': 2, 'EX_h2o_e': 9999, 'EX_co2_e': 9999, 'EX_nh4_e': 9999, 'EX_pi_e': 9999, 'EX_so4_e': 9999, 'EX_k_e': 9999, 'EX_na1_e': 9999}


# 1. The effect of limiting the rewiring in the standard medium

First test the protocol in a single case, set by idx. Recall that idx=-1 is the population growing in the standard medium, as media are sorted by env. richness (increasing).

In [ ]:
idx = -1
FLUX_MIN = 1e-10

print('With rewiring:')
print('Population mu: %1.4f +/- %1.4f' % (np.mean(MU[idx,:]), np.std(MU[idx,:]) ) )
print('R2_pps:  %1.4f' % (R2_pps[idx] ) )

with Q.model:
    # Apply wild type genotype
    Q.reset_dosage()
    Q.apply_dosage()
    
    # Apply medium and create media list
    Q.model.medium = MEDIA_LIST[idx]
    _media = [MEDIA_LIST[idx] for _ in range(G_std.shape[0])]
    
    
    wt_solution = Q.optimize()
    wt_flxes    = np.array([ wt_solution.fluxes[rxn] for rxn in Q.NEX_RXNS  ])
    print('[ WT mu=%1.3f ]' % wt_solution.fluxes[Q.BIOMASS_ID] )
    
    # For every null flux, fix it as null
    for ii in np.argwhere( np.abs(wt_flxes)<=FLUX_MIN)[:,0]:
        rxnid = np.array(Q.NEX_RXNS)[ii]
        Q.model.reactions.get_by_id(rxnid).upper_bound = 0
        Q.model.reactions.get_by_id(rxnid).lower_bound = 0
        
    _mu, _G, _J, _, _ = Q.compute_population( genotypes= G_std, media = _media , nprocessors=50)    
    
    #... clear inviable cases
    _mu, _G = Q.clear_population( _mu, [G_std,] , minimal_gr=1e-3)
    print('Computing PPS with %d individuals.' % len(_mu) )
    
    
    #... normalize population and compute PPS
    X   = _G  - np.mean( _G , axis=0)
    y   = _mu - np.mean( _mu )
    fit = LassoCV(fit_intercept = False , positive= False ).fit(X, y)

    # y vamos a guardar dos R2 distintos:
    print('Without rewiring:')
    print( 'Population mu: %1.4f +/- %1.4f' % (np.mean(_mu), np.std(_mu)) )
    print( 'R2:      %1.4f' % r2_score(y, fit.predict(X) ) )

With rewiring:
Population mu: 0.4075 +/- 0.0257
R2_pps:  0.2694
[ WT mu=0.514 ]
Computing population of 5000 samples...


 37%|███▋      | 1854/5000 [00:16<00:25, 122.54it/s]

#### [plot] Plot the results comparing with and w/o rewiring
Check that w/o rewiring leads to fitness costs in many individuals, and the PGS find additional large effect predictors.

In [ ]:
plt.figure( figsize=(15,4), facecolor='w', dpi=300)
plt.subplot(1,2,1)
plt.plot( MU[idx,:], _mu,'.')
plt.plot( MU[idx,:], MU[idx,:], 'k', lw=0.5)
plt.xlabel('Growth rate\nwith rewiring')
plt.ylabel('Growth rate\nwithout rewiring')
plt.grid()

plt.subplot(1,2,2)
plt.plot(BETAS[idx,:],fit.coef_,'.')
plt.plot(BETAS[idx,:],BETAS[idx,:],'k', lw=0.5)
plt.grid();
plt.xlabel('Effect size\nwith rewiring')
plt.ylabel('Effect size\nwithout rewiring')

plt.tight_layout();

# 2. Limiting the rewiring in all valid media...

## ... load data


In [ ]:
data = np.load('Data_Sup_rewiring_randomenv.npz')
Delta_MU = data['Delta_MU']
Delta_R2 = data['Delta_R2']

print('Infeasibles: ', np.sum(np.isnan(Delta_MU)))
print( 'Total: ', len(Delta_MU))



In [ ]:
idx = np.isfinite(Delta_MU)

plt.figure( figsize=(8,5))
plt.plot(Delta_MU, Delta_R2,'.')
plt.text(-0.047, 0.0, r'$\rho = %1.2f$' % np.corrcoef(Delta_MU[idx], Delta_R2[idx])[0,1] )
plt.grid()
plt.xlabel('$\Delta\mu$')
plt.ylabel('$\Delta R^2$')

print("Fraction feasible %d %%" % (100*np.sum(idx)/ len(idx)) )
print( np.corrcoef( Delta_MU[idx], Delta_R2[idx])[0,1] )